In [1]:
# bert multi
from transformers import CamembertTokenizer, CamembertModel, AutoTokenizer, AutoModel,AutoModelForSequenceClassification, utils, BertModel, BertTokenizer
import torch
from scipy.spatial.distance import cosine
from bertviz import model_view, head_view
import itertools
from IPython import display
import matplotlib.pyplot as plt
import numpy as np
#utils.logging.set_verbosity_error()  # Suppress standard warnings

c:\Users\Etudiant\M1_TAL\m1-supervised-project\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Initialisation du tokenizer et du modèle BERT multilingue
model_version = 'bert-base-multilingual-cased'
tokenizer = BertTokenizer.from_pretrained(model_version)
model = BertModel.from_pretrained(model_version, output_attentions=True)


# Phrases avec le verbe 'courir'
phrases = [
    "Il court un péril en allant là-bas.",
    "Le buzz court sur les réseaux sociaux.",
    "Le bruit court dans les couloirs.",
    "Elle court sur la route.",
    "Le danger court dans les zones inexplorées.",
    "Le nuage court dans le ciel orageux.",
    "Le risque court dans chaque décision d'investissement."
]

"""
# Phrases avec le verbe 'faire'
phrases = [
    "Il fait marche arrière concernant ma décision.",
    "Elle fait la lessive tous les samedis pour garder mes vêtements propres.",
    "Julien fait du vélo tous les matins pour rester en forme.",
    "Il fait souvent du cinéma pour attirer la pitié.",
    "On fait une demande officielle pour obtenir l'autorisation nécessaire.",
    "Coralie fait de la boxe pour améliorer ma condition physique et ma concentration."
]
"""
# Verbe à analyser
word = 'court'  # 'fait'

# Comparer chaque paire de phrases
for phrase1, phrase2 in itertools.combinations(phrases, 2):
    tokens1 = [token.lower() for token in tokenizer.tokenize(phrase1)]
    tokens2 = [token.lower() for token in tokenizer.tokenize(phrase2)]

    index_word1 = next((i for i, token in enumerate(tokens1) if word in token), None)
    index_word2 = next((i for i, token in enumerate(tokens2) if word in token), None)

    if index_word1 is not None and index_word2 is not None:
        inputs1 = tokenizer.encode_plus(phrase1, return_tensors='pt')
        inputs2 = tokenizer.encode_plus(phrase2, return_tensors='pt')

        with torch.no_grad():
            outputs1 = model(**inputs1)
            outputs2 = model(**inputs2)

        embedding1 = outputs1.last_hidden_state[0, index_word1, :]
        embedding2 = outputs2.last_hidden_state[0, index_word2, :]

        similarity = 1 - cosine(embedding1.numpy(), embedding2.numpy())
        print(f"Similarity for '{word}' between '{phrase1}' and '{phrase2}': {similarity:.2f}")
    else:
        print(f"Impossible de calculer la similarité entre '{phrase1}' et '{phrase2}' car le mot '{word}' n'est pas trouvé dans une des deux phrases.")



c:\Users\Etudiant\M1_TAL\m1-supervised-project\.venv\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Similarity for 'court' between 'Il court un péril en allant là-bas.' and 'Le buzz court sur les réseaux sociaux.': 0.37
Similarity for 'court' between 'Il court un péril en allant là-bas.' and 'Le bruit court dans les couloirs.': 0.41
Similarity for 'court' between 'Il court un péril en allant là-bas.' and 'Elle court sur la route.': 0.62
Similarity for 'court' between 'Il court un péril en allant là-bas.' and 'Le danger court dans les zones inexplorées.': 0.41
Similarity for 'court' between 'Il court un péril en allant là-bas.' and 'Le nuage court dans le ciel orageux.': 0.47
Similarity for 'court' between 'Il court un péril en allant là-bas.' and 'Le risque court dans chaque décision d'investissement.': 0.39
Similarity for 'court' between 'Le buzz court sur les réseaux sociaux.' and 'Le bruit court dans les couloirs.': 0.44
Similarity for 'court' between 'Le buzz court sur les réseaux sociaux.' and 'Elle court sur la route.': 0.30
Similarity for 'court' between 'Le buzz court sur les

In [4]:
model.eval()

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(119547, 768, padding_idx=0)
    (position_embeddings): Embedding(512, 768)
    (token_type_embeddings): Embedding(2, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0-11): 12 x BertLayer(
        (attention): BertAttention(
          (self): BertSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): BertSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
            (dropout): Dropout(p=0.1, inplace=False)
 

BERTviz for BERT multilingual

In [3]:
model_version = 'bert-base-multilingual-cased'
model = BertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = BertTokenizer.from_pretrained(model_version)

sentence_a = "Le bruit court dans les couloirs"
sentence_b = "Elle court sur la route"
inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt')
input_ids = inputs['input_ids']
token_type_ids = inputs['token_type_ids']
attention = model(input_ids, token_type_ids=token_type_ids)[-1]
sentence_b_start = token_type_ids[0].tolist().index(1)
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list) 

head_view(attention, tokens, sentence_b_start)
model_view(attention, tokens, sentence_b_start, include_layers=[0,1,2,8,9])


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>